## Pretrained embeddings and fine tuining

From cell number 19 are present the results of the best fine tune models. If tou want to run all the code toghether from cell 19 you have to comment the code.
In the first cell we look at the pretrained embeddings available.

In [1]:
import gensim.downloader
import numpy as np
# Show all available models in gensim-data
gensim.downloader.info()['models'].keys()

dict_keys(['fasttext-wiki-news-subwords-300', 'conceptnet-numberbatch-17-06-300', 'word2vec-ruscorpora-300', 'word2vec-google-news-300', 'glove-wiki-gigaword-50', 'glove-wiki-gigaword-100', 'glove-wiki-gigaword-200', 'glove-wiki-gigaword-300', 'glove-twitter-25', 'glove-twitter-50', 'glove-twitter-100', 'glove-twitter-200', '__testing_word2vec-matrix-synopsis'])

In [ ]:

#Here we download one of the 4 pretrained models that we used 'word2vec-ruscorpora-300', 
# 'word2vec-google-news-300'  'glove-twitter-200'  'glove-wiki-gigaword-300'
google_model = gensim.downloader.load('word2vec-google-news-300')


In the cell below we define the path of the downloaded pretrained model, these paths represent the location of this embeddings in the machine were this notebook was executed. The paths have to be substituted with the correct location of the embeddings where this notebook is currently executing.

In [2]:
from gensim.models import KeyedVectors
EMBEDDING_FILE_GIGA= 'C:/Users/filip/gensim-data/glove-wiki-gigaword-300/glove-wiki-gigaword-300/glove-wiki-gigaword-300.txt'
EMBEDDING_FILE_GOOGLE = 'C:/Users/filip/gensim-data/word2vec-google-news-300/word2vec-google-news-300/GoogleNews-vectors-negative300.bin'
EMBEDDING_FILE_TW = 'C:/Users/filip/gensim-data/glove-twitter-200/glove-twitter-200/glove-twitter-200.txt'
EMBEDDING_FILE_RUSS = 'C:/Users/filip/gensim-data/word2vec-ruscorpora-300/word2vec-ruscorpora-300/word2vec-ruscorpora-300'



In [4]:
from sklearn.linear_model import LogisticRegression
from gensim.utils import simple_preprocess
from gensim.models import fasttext
from datautils import documents_vector
from datautils import documents_vector_pre
import datautils
from sklearn.model_selection import ParameterGrid
from sklearn.metrics import f1_score
import pandas as pd
from sklearn.linear_model import LogisticRegression
from gensim.utils import simple_preprocess
from gensim.models import Word2Vec
from datautils import documents_vector
from nltk.tokenize import word_tokenize
from transformers import AutoTokenizer
import nltk
from gensim.models import Word2Vec
from gensim.models import FastText
from nltk.tokenize import word_tokenize
import nltk
from gensim.models import Word2Vec
from nltk.tokenize import word_tokenize
PATH = './Dataset/power-gb-train.tsv'
RES_DIR = './Results/'


WE load our google model the best pretrained model that we found and we compute his scores

In [39]:
#we load the pretrained model
google_model = KeyedVectors.load_word2vec_format(EMBEDDING_FILE_GOOGLE, binary=True)
#we split the dataset
X_train, y_train, X_val, y_val, _, _ = datautils.split_holdout_dataset(PATH)

tr_fold = list(map(simple_preprocess, X_train))
val_fold = list(map(simple_preprocess, X_val))


#pooling
X_train1 = documents_vector_pre(tr_fold, google_model)
X_va1l = documents_vector_pre(val_fold, google_model)

we compute the word analogy for the pretrained model and we load the test file

In [40]:
import requests
url = "https://raw.githubusercontent.com/nicholas-leonard/word2vec/master/questions-words.txt"
test_file = 'questions-words.txt'
questions = requests.get(url).content.decode()
with open(test_file,mode='w',encoding='utf-8') as outputfile:
    outputfile.write(questions)
print(questions[:1000])

#word analogy with dummy4unknown
w2v_large_analogy_dummy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
#word analogy 
w2v_large_analogy = google_model.evaluate_word_analogies(test_file)


: capital-common-countries
Athens Greece Baghdad Iraq
Athens Greece Bangkok Thailand
Athens Greece Beijing China
Athens Greece Berlin Germany
Athens Greece Bern Switzerland
Athens Greece Cairo Egypt
Athens Greece Canberra Australia
Athens Greece Hanoi Vietnam
Athens Greece Havana Cuba
Athens Greece Helsinki Finland
Athens Greece Islamabad Pakistan
Athens Greece Kabul Afghanistan
Athens Greece London England
Athens Greece Madrid Spain
Athens Greece Moscow Russia
Athens Greece Oslo Norway
Athens Greece Ottawa Canada
Athens Greece Paris France
Athens Greece Rome Italy
Athens Greece Stockholm Sweden
Athens Greece Tehran Iran
Athens Greece Tokyo Japan
Baghdad Iraq Bangkok Thailand
Baghdad Iraq Beijing China
Baghdad Iraq Berlin Germany
Baghdad Iraq Bern Switzerland
Baghdad Iraq Cairo Egypt
Baghdad Iraq Canberra Australia
Baghdad Iraq Hanoi Vietnam
Baghdad Iraq Havana Cuba
Baghdad Iraq Helsinki Finland
Baghdad Iraq Islamabad Pakistan
Baghdad Iraq Kabul Afghanistan
Baghdad Iraq London England


In [41]:
#we take a look at the scores of word analogy
w2v_large_analogy[0]

0.7401448525607863

In [42]:
w2v_large_analogy[1]

[{'section': 'capital-common-countries',
  'correct': [('ATHENS', 'GREECE', 'BANGKOK', 'THAILAND'),
   ('ATHENS', 'GREECE', 'BEIJING', 'CHINA'),
   ('ATHENS', 'GREECE', 'BERLIN', 'GERMANY'),
   ('ATHENS', 'GREECE', 'BERN', 'SWITZERLAND'),
   ('ATHENS', 'GREECE', 'CAIRO', 'EGYPT'),
   ('ATHENS', 'GREECE', 'CANBERRA', 'AUSTRALIA'),
   ('ATHENS', 'GREECE', 'HAVANA', 'CUBA'),
   ('ATHENS', 'GREECE', 'HELSINKI', 'FINLAND'),
   ('ATHENS', 'GREECE', 'ISLAMABAD', 'PAKISTAN'),
   ('ATHENS', 'GREECE', 'MADRID', 'SPAIN'),
   ('ATHENS', 'GREECE', 'MOSCOW', 'RUSSIA'),
   ('ATHENS', 'GREECE', 'OSLO', 'NORWAY'),
   ('ATHENS', 'GREECE', 'OTTAWA', 'CANADA'),
   ('ATHENS', 'GREECE', 'PARIS', 'FRANCE'),
   ('ATHENS', 'GREECE', 'ROME', 'ITALY'),
   ('ATHENS', 'GREECE', 'STOCKHOLM', 'SWEDEN'),
   ('ATHENS', 'GREECE', 'TEHRAN', 'IRAN'),
   ('ATHENS', 'GREECE', 'TOKYO', 'JAPAN'),
   ('BAGHDAD', 'IRAQ', 'BANGKOK', 'THAILAND'),
   ('BAGHDAD', 'IRAQ', 'BEIJING', 'CHINA'),
   ('BAGHDAD', 'IRAQ', 'BERLIN', 'GERMA

In [43]:
#we take a look at the scores of word analogy with dummy for unknown
w2v_large_analogy_dummy[0]

0.7320405239459681

In [44]:
w2v_large_analogy_dummy[1]

[{'section': 'capital-common-countries',
  'correct': [('ATHENS', 'GREECE', 'BANGKOK', 'THAILAND'),
   ('ATHENS', 'GREECE', 'BEIJING', 'CHINA'),
   ('ATHENS', 'GREECE', 'BERLIN', 'GERMANY'),
   ('ATHENS', 'GREECE', 'BERN', 'SWITZERLAND'),
   ('ATHENS', 'GREECE', 'CAIRO', 'EGYPT'),
   ('ATHENS', 'GREECE', 'CANBERRA', 'AUSTRALIA'),
   ('ATHENS', 'GREECE', 'HAVANA', 'CUBA'),
   ('ATHENS', 'GREECE', 'HELSINKI', 'FINLAND'),
   ('ATHENS', 'GREECE', 'ISLAMABAD', 'PAKISTAN'),
   ('ATHENS', 'GREECE', 'MADRID', 'SPAIN'),
   ('ATHENS', 'GREECE', 'MOSCOW', 'RUSSIA'),
   ('ATHENS', 'GREECE', 'OSLO', 'NORWAY'),
   ('ATHENS', 'GREECE', 'OTTAWA', 'CANADA'),
   ('ATHENS', 'GREECE', 'PARIS', 'FRANCE'),
   ('ATHENS', 'GREECE', 'ROME', 'ITALY'),
   ('ATHENS', 'GREECE', 'STOCKHOLM', 'SWEDEN'),
   ('ATHENS', 'GREECE', 'TEHRAN', 'IRAN'),
   ('ATHENS', 'GREECE', 'TOKYO', 'JAPAN'),
   ('BAGHDAD', 'IRAQ', 'BANGKOK', 'THAILAND'),
   ('BAGHDAD', 'IRAQ', 'BEIJING', 'CHINA'),
   ('BAGHDAD', 'IRAQ', 'BERLIN', 'GERMA

In the cell below we apply a grid search over the hyperparameters of the logistic regression

In [7]:


from sklearn.metrics import recall_score
from sklearn.metrics import precision_score

#this grid search that is commented is for when you run the full code
'''
hyperparameters1 = {
        "penalty": ["l2"],
        "C": [0.1, 1.0, 10.0, 100.0, 1000.0,1500.0],
        "solver": ["lbfgs"],
        "max_iter": [100, 200, 500,700],
    }
'''
# here we saw the validation values for the best values
hyperparameters1 = {
        "penalty": ["l2"],
        "C": [1500.0],
        "solver": ["lbfgs"],
        "max_iter": [ 500],
    }

param_grid1 = list(ParameterGrid(hyperparameters1))

results_df = pd.DataFrame(
    columns=["penalty", "C", "solver", "max_iter", "F1 Score","Precision","Recall"]
)

for par1 in param_grid1:
            
        model = LogisticRegression(**par1)
        model.fit(X_train1, y_train)

        # Compute F1 score,Prediction and Recall on validation set
        y_val_pred = model.predict(X_va1l)
        f1_macro = f1_score(y_val, y_val_pred, average="macro")
        precision= precision_score(y_val,y_val_pred)
        recall=recall_score(y_val,y_val_pred)

        print(f"Parameters: {par1}")
        print(f"\tF1 score: {f1_macro}")
        print(f"\tRecall: {recall}")
        print(f"\tPrecision: {precision}")
        results_df = pd.concat(
            [
                results_df,
                pd.DataFrame(
                    {
                        "penalty": par1["penalty"],
                        "C": par1["C"],
                        "solver": par1["solver"],
                        "max_iter": par1["max_iter"],
                        "F1 Score": f1_macro,
                        "Precision": precision,
                        "Recall":recall
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
#change the name when we change the pretrained model
results_df.to_csv(RES_DIR+f"results-Logistic-google.csv", index=False)

Parameters: {'C': 1500.0, 'max_iter': 500, 'penalty': 'l2', 'solver': 'lbfgs'}
	F1 score: 0.7246973722789278
	Recall: 0.8165245516024698
	Precision: 0.7425133689839573


C:\Users\filip\AppData\Local\Temp\ipykernel_26200\1007017138.py:42: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  results_df = pd.concat(


Here we defined a function for the fine tuning of a word2vec model using punkt tokenizer

In [ ]:
from nltk.tokenize import word_tokenize
import nltk
from gensim.models import Word2Vec

def w2v_tok(nome,dimensione,google_model):
    #we download the tokenizer
    nltk.download('punkt')

    #we define the word2vec model dimension the one of the pretrained emebedding
    finetuned_model = Word2Vec(vector_size=dimensione, min_count=1)
    #we split the dataset
    X_train, y_train, X_val, y_val, _, _ = datautils.split_holdout_dataset(PATH)

    #we use the tokenizer to tokenize our training set
    tokenized_corpus = [word_tokenize(sentence.lower()) for sentence in X_train]

    #we buld the vocabulary
    finetuned_model.build_vocab(tokenized_corpus)

    #we take the word that are common between our model and the pretrained
    intersecting_words = set(finetuned_model.wv.key_to_index.keys()) & set(google_model.key_to_index.keys())

    # Update the embeddings of the fine-tuned model with pre-trained embeddings for intersecting words
    for word in intersecting_words:
        finetuned_model.wv[word] = google_model[word]

    # Train the fine-tuned Word2Vec model
    finetuned_model.train(tokenized_corpus, total_examples=len(tokenized_corpus), epochs=10)
    finetuned_model.wv.save(f"./Embeddings/w2v-pretrained-tok-{nome}")

    tr_fold = list(map(simple_preprocess, X_train))
    val_fold = list(map(simple_preprocess, X_val))

    X_train1 = documents_vector(tr_fold, finetuned_model)
    X_va1l = documents_vector(val_fold, finetuned_model)
    

Here we defined a function for the fine tuning of a fasttext model using punkt tokenizer

In [3]:
from nltk.tokenize import word_tokenize
import nltk
from gensim.models import FastText
from gensim.models import Word2Vec

def ftx_tok(nome,dimensione,google_model):
    #we download the tokenizer
    nltk.download('punkt')

    #we define the fasttext model dimension the one of the pretrained emebedding
    finetuned_model = FastText(vector_size=dimensione, min_count=1)
    #we split the dataset
    X_train, y_train, X_val, y_val, _, _ = datautils.split_holdout_dataset(PATH)

    #we tokenize our training set
    tokenized_corpus = [word_tokenize(sentence.lower()) for sentence in X_train]
    #we build the vocabulary
    finetuned_model.build_vocab(tokenized_corpus)
    #we take the word that are common between our model and the pretrained
    intersecting_words = set(finetuned_model.wv.key_to_index.keys()) & set(google_model.key_to_index.keys())

    # Update the embeddings of the fine-tuned model with pre-trained embeddings for intersecting words
    for word in intersecting_words:
        finetuned_model.wv[word] = google_model[word]

    # Train the fine-tuned Word2Vec model
    finetuned_model.train(tokenized_corpus, total_examples=len(tokenized_corpus), epochs=10)

    finetuned_model.wv.save(f"./Embeddings/ftx-pretrained-tok-{nome}")

    tr_fold = list(map(simple_preprocess, X_train))
    val_fold = list(map(simple_preprocess, X_val))

    #pooling
    X_train1 = documents_vector(tr_fold, finetuned_model)
    X_va1l = documents_vector(val_fold, finetuned_model)


In the cell below is defined the function that make the fine tuning using the bert based tokenizer. We fine tuned a word2vec model

In [4]:
from nltk.tokenize import word_tokenize
from transformers import AutoTokenizer
import nltk
from gensim.models import Word2Vec
from gensim.models import FastText


def w2v_huggin(nome,dimensione,google_model):
    nltk.download('punkt')

    #we take the tokenier from bert
    tokenizer = AutoTokenizer.from_pretrained("bert-base-uncased")

    #we create a word2vec model
    finetuned_model = Word2Vec(vector_size=dimensione, min_count=1)
    #we split the dataset
    X_train, y_train, X_val, y_val, _, _ = datautils.split_holdout_dataset(PATH)

    #we tokenize
    tokenized_corpus = [tokenizer.tokenize(sentence.lower()) for sentence in X_train]
    #we build the vocabulary
    finetuned_model.build_vocab(tokenized_corpus)

    #we take the words that are common between our model vocabulartìy and the pretrained model
    intersecting_words = set(finetuned_model.wv.key_to_index.keys()) & set(google_model.key_to_index.keys())

    # Update the embeddings of the fine-tuned model with pre-trained embeddings for intersecting words
    for word in intersecting_words:
        finetuned_model.wv[word] = google_model[word]

    # Train the fine-tuned Word2Vec model
    finetuned_model.train(tokenized_corpus, total_examples=len(tokenized_corpus), epochs=10)
    #we save the model
    finetuned_model.wv.save(f"./Embeddings/w2v-pretrained-huggin-{nome}")

    tr_fold = list(map(simple_preprocess, X_train))
    val_fold = list(map(simple_preprocess, X_val))

    #we apply the pooling
    X_train1 = documents_vector(tr_fold, finetuned_model)
    X_va1l = documents_vector(val_fold, finetuned_model)
   

In the cell below is defined the function that make the fine tuning using the bert based tokenizer. We fine tuned a fasttext model

In [5]:
from nltk.tokenize import word_tokenize
from transformers import AutoTokenizer
import nltk
from gensim.models import Word2Vec
from gensim.models import FastText

def ftx_hug(nome,dimensione,google_model):

    nltk.download('punkt')

    #we take the tokenier from bert
    tokenizer = AutoTokenizer.from_pretrained("bert-base-uncased")

    #we create a fasttext model
    finetuned_model = FastText(vector_size=dimensione, min_count=1)
    #we split the dataset in training and validation
    X_train, y_train, X_val, y_val, _, _ = datautils.split_holdout_dataset(PATH)

    #we tokenize
    tokenized_corpus = [tokenizer.tokenize(sentence.lower()) for sentence in X_train]
    #we build the vocabulary
    finetuned_model.build_vocab(tokenized_corpus)

    #we take the common word from our model and the pretrained model
    intersecting_words = set(finetuned_model.wv.key_to_index.keys()) & set(google_model.key_to_index.keys())

    # Update the embeddings of the fine-tuned model with pre-trained embeddings for intersecting words
    for word in intersecting_words:
        finetuned_model.wv[word] = google_model[word]

    # Train the fine-tuned Fasttex model
    finetuned_model.train(tokenized_corpus, total_examples=len(tokenized_corpus), epochs=10)
    #we save it
    finetuned_model.wv.save(f"./Embeddings/ftx-pretrained-huggin-{nome}")

    tr_fold = list(map(simple_preprocess, X_train))
    val_fold = list(map(simple_preprocess, X_val))

    #we procede with the pooling
    X_train1 = documents_vector(tr_fold, finetuned_model)
    X_va1l = documents_vector(val_fold, finetuned_model)

    

We took everyone of our models and we compute we apply the fine tuning with to our models(word2vec and fasttext) using 2 different tokenizer

In [ ]:
vet=[EMBEDDING_FILE_GOOGLE,EMBEDDING_FILE_GIGA,EMBEDDING_FILE_TW,EMBEDDING_FILE_RUSS]
for i in range(0,4):
    
    if(i==0 or i==3):
        #here we put binary equals to true because 'google-news-300' and 'russ corpora 300'gives a binary file
        google_model = KeyedVectors.load_word2vec_format(vet[i], binary=True)
        if(i==0):
            #fine tuning with google news 300
            w2v_tok('google',300,google_model)
            w2v_huggin('google',300,google_model)
            ftx_hug('google',300,google_model)
            ftx_tok('google',300,google_model)
        else:
            #fine tuning with russ corpora 300
            w2v_tok('russ',300,google_model)
            w2v_huggin('russ',300,google_model)
            ftx_hug('russ',300,google_model)
            ftx_tok('russ',300,google_model)
    else:

        #here we put binary equals to true because 'glove-twitter-200' and 'glove wiki gigaword 300'gives a binary file
        google_model= KeyedVectors.load_word2vec_format(vet[i], binary=False)
        if(i==2):
            #fine tuning with twitter
            w2v_tok('twitter',200,google_model)
            w2v_huggin('twitter',200,google_model)
            ftx_hug('twitter',200,google_model)
            ftx_tok('twitter',200,google_model)
        else:
            #fine tuning with gigaword 300
            w2v_tok('giga',300,google_model)
            w2v_huggin('giga',300,google_model)
            ftx_hug('giga',300,google_model)
            ftx_tok('giga',300,google_model)
    

In the cell below we evaluate on the validation set the fine tuned models. We apply a grid search over the possible hyperparameters of the logistic regression. We took only the fasttext fine tuned models

In [ ]:
from sklearn.metrics import recall_score
from sklearn.metrics import precision_score
from gensim.models import KeyedVectors

#we take the the fasttext finte tuned model and we run them ove a logistic regression
vet=['Embeddings/ftx-pretrained-tok-giga','Embeddings/ftx-pretrained-huggin-giga',
     'Embeddings/ftx-pretrained-tok-twitter','Embeddings/ftx-pretrained-huggin-twitter',
     'Embeddings/ftx-pretrained-tok-google','Embeddings/ftx-pretrained-huggin-google',
     'Embeddings/ftx-pretrained-tok-russ','Embeddings/ftx-pretrained-huggin-russ']

for i in range(0,8):
    
    #we load the fine tuned model
    finetuned_model=model = KeyedVectors.load(vet[i])

    # we split the data set into training and validation set
    X_train, y_train, X_val, y_val, _, _ = datautils.split_holdout_dataset(PATH)


    tr_fold = list(map(simple_preprocess, X_train))
    val_fold = list(map(simple_preprocess, X_val))

    #we apply the pooling
    X_train1 = documents_vector_pre(tr_fold, finetuned_model)
    X_va1l = documents_vector_pre(val_fold, finetuned_model)


    #definition of the hyperparameters of the logistic regression
    hyperparameters1 = {
            "penalty": ["l2"],
            "C": [0.1, 1.0, 10.0, 100.0, 1000.0,1500.0],
            "solver": ["lbfgs"],
            "max_iter": [100, 200, 500,700],
        }

    param_grid1 = list(ParameterGrid(hyperparameters1))

    results_df = pd.DataFrame(
        columns=["penalty", "C", "solver", "max_iter", "F1 Score","Precision","Recall"]
    )

    for par1 in param_grid1:
            #we create and train the logistic regression
            model = LogisticRegression(**par1)
            model.fit(X_train1, y_train)

            # Compute F1 score, Precison and Recall on validation set
            y_val_pred = model.predict(X_va1l)
            f1_macro = f1_score(y_val, y_val_pred, average="macro")
            precision= precision_score(y_val,y_val_pred)
            recall=recall_score(y_val,y_val_pred)

            print(f"Parameters: {par1}")
            print(f"\tF1 score: {f1_macro}")
            #we save everything in the dataframe
            results_df = pd.concat(
                [
                    results_df,
                    pd.DataFrame(
                        {
                            "penalty": par1["penalty"],
                            "C": par1["C"],
                            "solver": par1["solver"],
                            "max_iter": par1["max_iter"],
                            "F1 Score": f1_macro,
                            "Precision": precision,
                            "Recall":recall
                            },
                        index=[0],
                        ),
                    ],
                    ignore_index=True,
                )

    # we export the dataframe to csv
    #for ponkt tokenizer
    if(i==0):
        results_df.to_csv(RES_DIR+f"results-Logistic-ftx-pretrained-tok-giga.csv", index=False)
    if(i==2):
        results_df.to_csv(RES_DIR+f"results-Logistic-ftx-pretrained-tok-twitter.csv", index=False)
    if(i==4):
        results_df.to_csv(RES_DIR+f"results-Logistic-ftx-pretrained-tok-google.csv", index=False)
    if(i==6):
        results_df.to_csv(RES_DIR+f"results-Logistic-ftx-pretrained-tok-russ.csv", index=False)
    #for hugginface tokenizer
    if(i==1):
        results_df.to_csv(RES_DIR+f"results-Logistic-ftx-pretrained-huggin-giga.csv", index=False)
    if(i==3):
        results_df.to_csv(RES_DIR+f"results-Logistic-ftx-pretrained-huggin-twitter.csv", index=False)
    if(i==5):
        results_df.to_csv(RES_DIR+f"results-Logistic-ftx-pretrained-huggin-google.csv", index=False)
    if(i==7):
        results_df.to_csv(RES_DIR+f"results-Logistic-ftx-pretrained-huggin-russ.csv", index=False)

In the cell below we evaluate on the validation set the fine tuned models. We apply a grid search over the possible hyperparameters of the logistic regression. We took only the word2vec fine tuned models

In [ ]:
from sklearn.metrics import recall_score
from sklearn.metrics import precision_score
from gensim.models import KeyedVectors

#we take the the word2vec fine tuned model and we run them ove a logistic regression
vet=['Embeddings/w2v-pretrained-tok-giga','Embeddings/w2v-pretrained-huggin-giga',
     'Embeddings/w2v-pretrained-tok-twitter','Embeddings/w2v-pretrained-huggin-twitter',
     'Embeddings/w2v-pretrained-tok-google','Embeddings/w2v-pretrained-huggin-google',
     'Embeddings/w2v-pretrained-tok-russ','Embeddings/w2v-pretrained-huggin-russ']

for i in range(0,8):
    #we load the fine tuned model
    finetuned_model=model = KeyedVectors.load(vet[i])

    # we split the data set into training and validation set
    X_train, y_train, X_val, y_val, _, _ = datautils.split_holdout_dataset(PATH)


    tr_fold = list(map(simple_preprocess, X_train))
    val_fold = list(map(simple_preprocess, X_val))

    #we apply the pooling
    X_train1 = documents_vector_pre(tr_fold, finetuned_model)
    X_va1l = documents_vector_pre(val_fold, finetuned_model)


    #definition of the hyperparameters of the logistic regression
    hyperparameters1 = {
            "penalty": ["l2"],
            "C": [0.1, 1.0, 10.0, 100.0, 1000.0,1500.0],
            "solver": ["lbfgs"],
            "max_iter": [100, 200, 500,700],
        }

    param_grid1 = list(ParameterGrid(hyperparameters1))

    results_df = pd.DataFrame(
        columns=["penalty", "C", "solver", "max_iter", "F1 Score","Precision","Recall"]
    )

    for par1 in param_grid1:
            #we create and train the logistic regression
            model = LogisticRegression(**par1)
            model.fit(X_train1, y_train)

            # Compute F1 score, Precison and Recall on validation set
            y_val_pred = model.predict(X_va1l)
            f1_macro = f1_score(y_val, y_val_pred, average="macro")
            precision= precision_score(y_val,y_val_pred)
            recall=recall_score(y_val,y_val_pred)

            print(f"Parameters: {par1}")
            print(f"\tF1 score: {f1_macro}")
            #we save everything in the dataframe
            results_df = pd.concat(
                [
                    results_df,
                    pd.DataFrame(
                        {
                            "penalty": par1["penalty"],
                            "C": par1["C"],
                            "solver": par1["solver"],
                            "max_iter": par1["max_iter"],
                            "F1 Score": f1_macro,
                            "Precision": precision,
                            "Recall":recall
                            },
                        index=[0],
                        ),
                    ],
                    ignore_index=True,
                )

    # we export the dataframe to csv
    if(i==0):
        results_df.to_csv(RES_DIR+f"results-Logistic-w2v-pretrained-tok-giga.csv", index=False)
    if(i==2):
        results_df.to_csv(RES_DIR+f"results-Logistic-w2v-pretrained-tok-twitter.csv", index=False)
    if(i==4):
        results_df.to_csv(RES_DIR+f"results-Logistic-w2v-pretrained-tok-google.csv", index=False)
    if(i==6):
        results_df.to_csv(RES_DIR+f"results-Logistic-w2v-pretrained-tok-russ.csv", index=False)
    #for hugginface tokenizer
    if(i==1):
        results_df.to_csv(RES_DIR+f"results-Logistic-w2v-pretrained-huggin-giga.csv", index=False)
    if(i==3):
        results_df.to_csv(RES_DIR+f"results-Logistic-w2v-pretrained-huggin-twitter.csv", index=False)
    if(i==5):
        results_df.to_csv(RES_DIR+f"results-Logistic-w2v-pretrained-huggin-google.csv", index=False)
    if(i==7):
        results_df.to_csv(RES_DIR+f"results-Logistic-w2v-pretrained-huggin-russ.csv", index=False)

Here we compute the word analogy for every fasttext fine tuned model

In [ ]:

#we take the the fasttext fine tuned model and we compute the word analogy
vet=['Embeddings/ftx-pretrained-tok-giga','Embeddings/ftx-pretrained-huggin-giga',
     'Embeddings/ftx-pretrained-tok-twitter','Embeddings/ftx-pretrained-huggin-twitter',
     'Embeddings/ftx-pretrained-tok-google','Embeddings/ftx-pretrained-huggin-google',
     'Embeddings/ftx-pretrained-tok-russ','Embeddings/ftx-pretrained-huggin-russ']


analogie = pd.DataFrame(
    columns=["Model", "Accuracy"]
)

for i in range(0,8):
    
    if(i==0):

        #we load the model 
        google_model = KeyedVectors.load(vet[i])
        #we evaluate with word analogy
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        #we put the result on a dataframe
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                        "Model":'ftx-giga-tok-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        #we compute the word analogy with dummy for unknown
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)

        #we crate the dataframe
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                        "Model":'ftx-giga-tok-true',
                        'Accuracy':w2v_large_analogy[0]
                    },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        
    if(i==1):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-giga-hug-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)

        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-giga-hug-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        
    if(i==2):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-twitter-tok-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-twitter-tok-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
    if(i==3):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-twitter-hug-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-twitter-hug-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
    if(i==4):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-google-tok-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-google-tok-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
    if(i==5):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-google-hug-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-google-hug-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
    if(i==6):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    { 
                        "Model":'ftx-russ-tok-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-russ-tok-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
    if(i==7):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-russ-hug-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'ftx-russ-hug-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )

analogie.to_csv("word_analogies_ftx.csv", index=False)

Here we compute the word analogy for every fasttext fine tuned model

In [ ]:
#we take the the word2vec fine tuned model and we compute the word analogy
vet=['Embeddings/w2v-pretrained-tok-giga','Embeddings/w2v-pretrained-huggin-giga',
     'Embeddings/w2v-pretrained-tok-twitter','Embeddings/w2v-pretrained-huggin-twitter',
     'Embeddings/w2v-pretrained-tok-google','Embeddings/w2v-pretrained-huggin-google',
     'Embeddings/w2v-pretrained-tok-russ','Embeddings/w2v-pretrained-huggin-russ']


analogie = pd.DataFrame(
    columns=["Model", "Accuracy"]
)

for i in range(0,8):
    
    if(i==0):

        #we load the model as keyvector object
        google_model = KeyedVectors.load(vet[i])
        #we compute the word analogy
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        #we save the scores in a dataframe
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                        "Model":'w2v-giga-tok-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        #we compute the word analogy with dummy4unknown 
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)

        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                        "Model":'w2v-giga-tok-true',
                        'Accuracy':w2v_large_analogy[0]
                    },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        
    if(i==1):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-giga-hug-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)

        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-giga-hug-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        
    if(i==2):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-twitter-tok-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-twitter-tok-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
    if(i==3):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-twitter-hug-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-twitter-hug-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
    if(i==4):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-google-tok-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-google-tok-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
    if(i==5):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-google-hug-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-google-hug-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
    if(i==6):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    { 
                        "Model":'w2v-russ-tok-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-russ-tok-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
    if(i==7):
        google_model = KeyedVectors.load(vet[i])
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-russ-hug-false',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )
        w2v_large_analogy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)
        analogie = pd.concat(
            [
                analogie,
                pd.DataFrame(
                    {
                         "Model":'w2v-russ-hug-true',
                        'Accuracy':w2v_large_analogy[0]
                        },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )

analogie.to_csv("word_analogies_w2v.csv", index=False)

This cell below if you run the all code do not have to be runned. Here we load our best fine tuned model with the best hyperparameters that we found

Here validation for fast text fine tuned model using wordpiece tokenizer

In [45]:
# we load the model, but this is not present in the file we send
finetuned_model=model = KeyedVectors.load('Embeddings/ftx-pretrained-huggin-google')

# we split the data set into training and validation set
X_train, y_train, X_val, y_val, _, _ = datautils.split_holdout_dataset(PATH)


tr_fold = list(map(simple_preprocess, X_train))
val_fold = list(map(simple_preprocess, X_val))

#we apply the pooling
X_train1 = documents_vector_pre(tr_fold, finetuned_model)
X_va1l = documents_vector_pre(val_fold, finetuned_model)


#definition of the hyperparameters of the logistic regression we took only the best for the validation scores here
hyperparameters1 = {
        "penalty": ["l2"],
        "C": [ 10.0],
        "solver": ["lbfgs"],
        "max_iter": [200],
    }

param_grid1 = list(ParameterGrid(hyperparameters1))

results_df = pd.DataFrame(
    columns=["penalty", "C", "solver", "max_iter", "F1 Score","Precision","Recall"]
)

for par1 in param_grid1:
        #we create and train the logistic regression
        model = LogisticRegression(**par1)
        model.fit(X_train1, y_train)

        # Compute F1 score, Precison and Recall on validation set
        y_val_pred = model.predict(X_va1l)
        f1_macro = f1_score(y_val, y_val_pred, average="macro")
        precision= precision_score(y_val,y_val_pred)
        recall=recall_score(y_val,y_val_pred)

        print(f"Parameters: {par1}")
        print(f"\tF1 score: {f1_macro}")
        print(f"\tRecall: {recall}")
        print(f"\tprecision: {precision}")
        #we save everything in the dataframe
        results_df = pd.concat(
            [
                results_df,
                pd.DataFrame(
                    {
                        "penalty": par1["penalty"],
                        "C": par1["C"],
                        "solver": par1["solver"],
                        "max_iter": par1["max_iter"],
                        "F1 Score": f1_macro,
                        "Precision": precision,
                        "Recall":recall
                            },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )


Parameters: {'C': 10.0, 'max_iter': 200, 'penalty': 'l2', 'solver': 'lbfgs'}
	F1 score: 0.7264033600657687
	Recall: 0.8197588944428109
	precision: 0.743268461743535


c:\Users\filip\Downloads\NLP-project-main (1)\NLP-project-main\hltvenv\Lib\site-packages\sklearn\linear_model\_logistic.py:469: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\filip\AppData\Local\Temp\ipykernel_26200\1821818452.py:46: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  results_df = pd.concat(


word analogy of the loaded model

In [46]:
google_model = finetuned_model
w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
w2v_large_analogy_dummy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)

In [47]:
w2v_large_analogy[0]

0.4860725567148464

In [48]:
w2v_large_analogy[1]

[{'section': 'capital-common-countries',
  'correct': [('BAGHDAD', 'IRAQ', 'TEHRAN', 'IRAN'),
   ('BEIJING', 'CHINA', 'MOSCOW', 'RUSSIA'),
   ('BEIJING', 'CHINA', 'TEHRAN', 'IRAN'),
   ('CAIRO', 'EGYPT', 'TEHRAN', 'IRAN'),
   ('MOSCOW', 'RUSSIA', 'TEHRAN', 'IRAN'),
   ('STOCKHOLM', 'SWEDEN', 'TEHRAN', 'IRAN')],
  'incorrect': [('ATHENS', 'GREECE', 'BAGHDAD', 'IRAQ'),
   ('ATHENS', 'GREECE', 'BANGKOK', 'THAILAND'),
   ('ATHENS', 'GREECE', 'BEIJING', 'CHINA'),
   ('ATHENS', 'GREECE', 'BERLIN', 'GERMANY'),
   ('ATHENS', 'GREECE', 'BERN', 'SWITZERLAND'),
   ('ATHENS', 'GREECE', 'CAIRO', 'EGYPT'),
   ('ATHENS', 'GREECE', 'CANBERRA', 'AUSTRALIA'),
   ('ATHENS', 'GREECE', 'HANOI', 'VIETNAM'),
   ('ATHENS', 'GREECE', 'HAVANA', 'CUBA'),
   ('ATHENS', 'GREECE', 'HELSINKI', 'FINLAND'),
   ('ATHENS', 'GREECE', 'ISLAMABAD', 'PAKISTAN'),
   ('ATHENS', 'GREECE', 'KABUL', 'AFGHANISTAN'),
   ('ATHENS', 'GREECE', 'LONDON', 'ENGLAND'),
   ('ATHENS', 'GREECE', 'MADRID', 'SPAIN'),
   ('ATHENS', 'GREECE', '

In [49]:
w2v_large_analogy_dummy[0]

0.2598239869013508

In [50]:
w2v_large_analogy_dummy[1]

[{'section': 'capital-common-countries',
  'correct': [('BAGHDAD', 'IRAQ', 'TEHRAN', 'IRAN'),
   ('BEIJING', 'CHINA', 'MOSCOW', 'RUSSIA'),
   ('BEIJING', 'CHINA', 'TEHRAN', 'IRAN'),
   ('CAIRO', 'EGYPT', 'TEHRAN', 'IRAN'),
   ('MOSCOW', 'RUSSIA', 'TEHRAN', 'IRAN'),
   ('STOCKHOLM', 'SWEDEN', 'TEHRAN', 'IRAN')],
  'incorrect': [('ATHENS', 'GREECE', 'BAGHDAD', 'IRAQ'),
   ('ATHENS', 'GREECE', 'BANGKOK', 'THAILAND'),
   ('ATHENS', 'GREECE', 'BEIJING', 'CHINA'),
   ('ATHENS', 'GREECE', 'BERLIN', 'GERMANY'),
   ('ATHENS', 'GREECE', 'BERN', 'SWITZERLAND'),
   ('ATHENS', 'GREECE', 'CAIRO', 'EGYPT'),
   ('ATHENS', 'GREECE', 'CANBERRA', 'AUSTRALIA'),
   ('ATHENS', 'GREECE', 'HANOI', 'VIETNAM'),
   ('ATHENS', 'GREECE', 'HAVANA', 'CUBA'),
   ('ATHENS', 'GREECE', 'HELSINKI', 'FINLAND'),
   ('ATHENS', 'GREECE', 'ISLAMABAD', 'PAKISTAN'),
   ('ATHENS', 'GREECE', 'KABUL', 'AFGHANISTAN'),
   ('ATHENS', 'GREECE', 'LONDON', 'ENGLAND'),
   ('ATHENS', 'GREECE', 'MADRID', 'SPAIN'),
   ('ATHENS', 'GREECE', '

Here validation scores for fast text fine tuned model using punkt tokenizer

In [51]:
# we load the model, but this is not present in the file we send
finetuned_model=model = KeyedVectors.load('Embeddings/ftx-pretrained-tok-google')

# we split the data set into training and validation set
X_train, y_train, X_val, y_val, _, _ = datautils.split_holdout_dataset(PATH)


tr_fold = list(map(simple_preprocess, X_train))
val_fold = list(map(simple_preprocess, X_val))

#we apply the pooling
X_train1 = documents_vector_pre(tr_fold, finetuned_model)
X_va1l = documents_vector_pre(val_fold, finetuned_model)


#definition of the hyperparameters of the logistic regression we took only the best for the validation scores here
hyperparameters1 = {
        "penalty": ["l2"],
        "C": [ 1500.0],
        "solver": ["lbfgs"],
        "max_iter": [700],
    }

param_grid1 = list(ParameterGrid(hyperparameters1))

results_df = pd.DataFrame(
    columns=["penalty", "C", "solver", "max_iter", "F1 Score","Precision","Recall"]
)

for par1 in param_grid1:
        #we create and train the logistic regression
        model = LogisticRegression(**par1)
        model.fit(X_train1, y_train)

        # Compute F1 score, Precison and Recall on validation set
        y_val_pred = model.predict(X_va1l)
        f1_macro = f1_score(y_val, y_val_pred, average="macro")
        precision= precision_score(y_val,y_val_pred)
        recall=recall_score(y_val,y_val_pred)

        print(f"Parameters: {par1}")
        print(f"\tF1 score: {f1_macro}")
        print(f"\tRecall: {recall}")
        print(f"\tprecision: {precision}")
        #we save everything in the dataframe
        results_df = pd.concat(
            [
                results_df,
                pd.DataFrame(
                    {
                        "penalty": par1["penalty"],
                        "C": par1["C"],
                        "solver": par1["solver"],
                        "max_iter": par1["max_iter"],
                        "F1 Score": f1_macro,
                        "Precision": precision,
                        "Recall":recall
                            },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )


Parameters: {'C': 1500.0, 'max_iter': 700, 'penalty': 'l2', 'solver': 'lbfgs'}
	F1 score: 0.7253988217421053
	Recall: 0.818582769773596
	precision: 0.7425980261403041


C:\Users\filip\AppData\Local\Temp\ipykernel_26200\3411256389.py:46: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  results_df = pd.concat(


In [52]:
google_model = finetuned_model
w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
w2v_large_analogy_dummy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)

In [53]:
w2v_large_analogy[0]

0.35719850420691807

In [54]:
w2v_large_analogy[1]

[{'section': 'capital-common-countries',
  'correct': [('BAGHDAD', 'IRAQ', 'TEHRAN', 'IRAN'),
   ('MOSCOW', 'RUSSIA', 'TEHRAN', 'IRAN')],
  'incorrect': [('ATHENS', 'GREECE', 'BAGHDAD', 'IRAQ'),
   ('ATHENS', 'GREECE', 'BANGKOK', 'THAILAND'),
   ('ATHENS', 'GREECE', 'BEIJING', 'CHINA'),
   ('ATHENS', 'GREECE', 'BERLIN', 'GERMANY'),
   ('ATHENS', 'GREECE', 'BERN', 'SWITZERLAND'),
   ('ATHENS', 'GREECE', 'CAIRO', 'EGYPT'),
   ('ATHENS', 'GREECE', 'CANBERRA', 'AUSTRALIA'),
   ('ATHENS', 'GREECE', 'HANOI', 'VIETNAM'),
   ('ATHENS', 'GREECE', 'HAVANA', 'CUBA'),
   ('ATHENS', 'GREECE', 'HELSINKI', 'FINLAND'),
   ('ATHENS', 'GREECE', 'ISLAMABAD', 'PAKISTAN'),
   ('ATHENS', 'GREECE', 'KABUL', 'AFGHANISTAN'),
   ('ATHENS', 'GREECE', 'LONDON', 'ENGLAND'),
   ('ATHENS', 'GREECE', 'MADRID', 'SPAIN'),
   ('ATHENS', 'GREECE', 'MOSCOW', 'RUSSIA'),
   ('ATHENS', 'GREECE', 'OSLO', 'NORWAY'),
   ('ATHENS', 'GREECE', 'OTTAWA', 'CANADA'),
   ('ATHENS', 'GREECE', 'PARIS', 'FRANCE'),
   ('ATHENS', 'GREECE',

In [55]:
w2v_large_analogy_dummy[0]

0.23459885386819485

In [56]:
w2v_large_analogy_dummy[1]

[{'section': 'capital-common-countries',
  'correct': [('BAGHDAD', 'IRAQ', 'TEHRAN', 'IRAN'),
   ('MOSCOW', 'RUSSIA', 'TEHRAN', 'IRAN')],
  'incorrect': [('ATHENS', 'GREECE', 'BAGHDAD', 'IRAQ'),
   ('ATHENS', 'GREECE', 'BANGKOK', 'THAILAND'),
   ('ATHENS', 'GREECE', 'BEIJING', 'CHINA'),
   ('ATHENS', 'GREECE', 'BERLIN', 'GERMANY'),
   ('ATHENS', 'GREECE', 'BERN', 'SWITZERLAND'),
   ('ATHENS', 'GREECE', 'CAIRO', 'EGYPT'),
   ('ATHENS', 'GREECE', 'CANBERRA', 'AUSTRALIA'),
   ('ATHENS', 'GREECE', 'HANOI', 'VIETNAM'),
   ('ATHENS', 'GREECE', 'HAVANA', 'CUBA'),
   ('ATHENS', 'GREECE', 'HELSINKI', 'FINLAND'),
   ('ATHENS', 'GREECE', 'ISLAMABAD', 'PAKISTAN'),
   ('ATHENS', 'GREECE', 'KABUL', 'AFGHANISTAN'),
   ('ATHENS', 'GREECE', 'LONDON', 'ENGLAND'),
   ('ATHENS', 'GREECE', 'MADRID', 'SPAIN'),
   ('ATHENS', 'GREECE', 'MOSCOW', 'RUSSIA'),
   ('ATHENS', 'GREECE', 'OSLO', 'NORWAY'),
   ('ATHENS', 'GREECE', 'OTTAWA', 'CANADA'),
   ('ATHENS', 'GREECE', 'PARIS', 'FRANCE'),
   ('ATHENS', 'GREECE',

Here validation scores for word2vec fine tuned model using punkt tokenizer

In [57]:
# we load the model, but this is not present in the file we send
finetuned_model=model = KeyedVectors.load('Embeddings/w2v-pretrained-tok-google')

# we split the data set into training and validation set
X_train, y_train, X_val, y_val, _, _ = datautils.split_holdout_dataset(PATH)


tr_fold = list(map(simple_preprocess, X_train))
val_fold = list(map(simple_preprocess, X_val))

#we apply the pooling
X_train1 = documents_vector_pre(tr_fold, finetuned_model)
X_va1l = documents_vector_pre(val_fold, finetuned_model)


#definition of the hyperparameters of the logistic regression we took only the best for the validation scores here
hyperparameters1 = {
        "penalty": ["l2"],
        "C": [ 1000.0],
        "solver": ["lbfgs"],
        "max_iter": [100],
    }

param_grid1 = list(ParameterGrid(hyperparameters1))

results_df = pd.DataFrame(
    columns=["penalty", "C", "solver", "max_iter", "F1 Score","Precision","Recall"]
)

for par1 in param_grid1:
        #we create and train the logistic regression
        model = LogisticRegression(**par1)
        model.fit(X_train1, y_train)

        # Compute F1 score, Precison and Recall on validation set
        y_val_pred = model.predict(X_va1l)
        f1_macro = f1_score(y_val, y_val_pred, average="macro")
        precision= precision_score(y_val,y_val_pred)
        recall=recall_score(y_val,y_val_pred)

        print(f"Parameters: {par1}")
        print(f"\tF1 score: {f1_macro}")
        print(f"\tRecall: {recall}")
        print(f"\tprecision: {precision}")
        #we save everything in the dataframe
        results_df = pd.concat(
            [
                results_df,
                pd.DataFrame(
                    {
                        "penalty": par1["penalty"],
                        "C": par1["C"],
                        "solver": par1["solver"],
                        "max_iter": par1["max_iter"],
                        "F1 Score": f1_macro,
                        "Precision": precision,
                        "Recall":recall
                            },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )


Parameters: {'C': 1000.0, 'max_iter': 100, 'penalty': 'l2', 'solver': 'lbfgs'}
	F1 score: 0.7308160576602032
	Recall: 0.8259335489561893
	precision: 0.7458842272968667


c:\Users\filip\Downloads\NLP-project-main (1)\NLP-project-main\hltvenv\Lib\site-packages\sklearn\linear_model\_logistic.py:469: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\filip\AppData\Local\Temp\ipykernel_26200\3488488560.py:46: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  results_df = pd.concat(


In [58]:
google_model = finetuned_model
w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
w2v_large_analogy_dummy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)

In [59]:
w2v_large_analogy[0]

0.36506699906512935

In [60]:
w2v_large_analogy[1]

[{'section': 'capital-common-countries',
  'correct': [('ATHENS', 'GREECE', 'MADRID', 'SPAIN'),
   ('ATHENS', 'GREECE', 'ROME', 'ITALY'),
   ('BAGHDAD', 'IRAQ', 'KABUL', 'AFGHANISTAN'),
   ('BANGKOK', 'THAILAND', 'CAIRO', 'EGYPT'),
   ('BEIJING', 'CHINA', 'CAIRO', 'EGYPT'),
   ('BEIJING', 'CHINA', 'ISLAMABAD', 'PAKISTAN'),
   ('BEIJING', 'CHINA', 'TEHRAN', 'IRAN'),
   ('BEIJING', 'CHINA', 'TOKYO', 'JAPAN'),
   ('BERLIN', 'GERMANY', 'MADRID', 'SPAIN'),
   ('BERLIN', 'GERMANY', 'TOKYO', 'JAPAN'),
   ('BERN', 'SWITZERLAND', 'ROME', 'ITALY'),
   ('CAIRO', 'EGYPT', 'BEIJING', 'CHINA'),
   ('CANBERRA', 'AUSTRALIA', 'OTTAWA', 'CANADA'),
   ('HANOI', 'VIETNAM', 'MOSCOW', 'RUSSIA'),
   ('HANOI', 'VIETNAM', 'BEIJING', 'CHINA'),
   ('HANOI', 'VIETNAM', 'CAIRO', 'EGYPT'),
   ('HELSINKI', 'FINLAND', 'STOCKHOLM', 'SWEDEN'),
   ('KABUL', 'AFGHANISTAN', 'BERLIN', 'GERMANY'),
   ('MOSCOW', 'RUSSIA', 'TEHRAN', 'IRAN'),
   ('MOSCOW', 'RUSSIA', 'BEIJING', 'CHINA'),
   ('OTTAWA', 'CANADA', 'TOKYO', 'JAPAN'

In [61]:
w2v_large_analogy_dummy[0]

0.2397666803110929

In [62]:
w2v_large_analogy_dummy[1]

[{'section': 'capital-common-countries',
  'correct': [('ATHENS', 'GREECE', 'MADRID', 'SPAIN'),
   ('ATHENS', 'GREECE', 'ROME', 'ITALY'),
   ('BAGHDAD', 'IRAQ', 'KABUL', 'AFGHANISTAN'),
   ('BANGKOK', 'THAILAND', 'CAIRO', 'EGYPT'),
   ('BEIJING', 'CHINA', 'CAIRO', 'EGYPT'),
   ('BEIJING', 'CHINA', 'ISLAMABAD', 'PAKISTAN'),
   ('BEIJING', 'CHINA', 'TEHRAN', 'IRAN'),
   ('BEIJING', 'CHINA', 'TOKYO', 'JAPAN'),
   ('BERLIN', 'GERMANY', 'MADRID', 'SPAIN'),
   ('BERLIN', 'GERMANY', 'TOKYO', 'JAPAN'),
   ('BERN', 'SWITZERLAND', 'ROME', 'ITALY'),
   ('CAIRO', 'EGYPT', 'BEIJING', 'CHINA'),
   ('CANBERRA', 'AUSTRALIA', 'OTTAWA', 'CANADA'),
   ('HANOI', 'VIETNAM', 'MOSCOW', 'RUSSIA'),
   ('HANOI', 'VIETNAM', 'BEIJING', 'CHINA'),
   ('HANOI', 'VIETNAM', 'CAIRO', 'EGYPT'),
   ('HELSINKI', 'FINLAND', 'STOCKHOLM', 'SWEDEN'),
   ('KABUL', 'AFGHANISTAN', 'BERLIN', 'GERMANY'),
   ('MOSCOW', 'RUSSIA', 'TEHRAN', 'IRAN'),
   ('MOSCOW', 'RUSSIA', 'BEIJING', 'CHINA'),
   ('OTTAWA', 'CANADA', 'TOKYO', 'JAPAN'

Here validation scores for word2vec fine tuned model using wordpiece tokenizer

In [63]:
# we load the model, but this is not present in the file we send
finetuned_model=model = KeyedVectors.load('Embeddings/w2v-pretrained-huggin-google')

# we split the data set into training and validation set
X_train, y_train, X_val, y_val, _, _ = datautils.split_holdout_dataset(PATH)


tr_fold = list(map(simple_preprocess, X_train))
val_fold = list(map(simple_preprocess, X_val))

#we apply the pooling
X_train1 = documents_vector_pre(tr_fold, finetuned_model)
X_va1l = documents_vector_pre(val_fold, finetuned_model)


#definition of the hyperparameters of the logistic regression we took only the best for the validation scores here
hyperparameters1 = {
        "penalty": ["l2"],
        "C": [ 100.0],
        "solver": ["lbfgs"],
        "max_iter": [100],
    }

param_grid1 = list(ParameterGrid(hyperparameters1))

results_df = pd.DataFrame(
    columns=["penalty", "C", "solver", "max_iter", "F1 Score","Precision","Recall"]
)

for par1 in param_grid1:
        #we create and train the logistic regression
        model = LogisticRegression(**par1)
        model.fit(X_train1, y_train)

        # Compute F1 score, Precison and Recall on validation set
        y_val_pred = model.predict(X_va1l)
        f1_macro = f1_score(y_val, y_val_pred, average="macro")
        precision= precision_score(y_val,y_val_pred)
        recall=recall_score(y_val,y_val_pred)

        print(f"Parameters: {par1}")
        print(f"\tF1 score: {f1_macro}")
        print(f"\tRecall: {recall}")
        print(f"\tprecision: {precision}")
        #we save everything in the dataframe
        results_df = pd.concat(
            [
                results_df,
                pd.DataFrame(
                    {
                        "penalty": par1["penalty"],
                        "C": par1["C"],
                        "solver": par1["solver"],
                        "max_iter": par1["max_iter"],
                        "F1 Score": f1_macro,
                        "Precision": precision,
                        "Recall":recall
                            },
                    index=[0],
                    ),
                ],
                ignore_index=True,
            )


Parameters: {'C': 100.0, 'max_iter': 100, 'penalty': 'l2', 'solver': 'lbfgs'}
	F1 score: 0.7261522501497758
	Recall: 0.8262275801234931
	precision: 0.7410337552742616


c:\Users\filip\Downloads\NLP-project-main (1)\NLP-project-main\hltvenv\Lib\site-packages\sklearn\linear_model\_logistic.py:469: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\filip\AppData\Local\Temp\ipykernel_26200\1153976065.py:46: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  results_df = pd.concat(


In [64]:
google_model = finetuned_model
w2v_large_analogy = google_model.evaluate_word_analogies(test_file)
w2v_large_analogy_dummy = google_model.evaluate_word_analogies(test_file,dummy4unknown=True)

In [65]:
w2v_large_analogy[0]

0.3570402986503302

In [37]:
w2v_large_analogy[1]

[{'section': 'capital-common-countries',
  'correct': [('ATHENS', 'GREECE', 'ROME', 'ITALY'),
   ('BAGHDAD', 'IRAQ', 'KABUL', 'AFGHANISTAN'),
   ('BERLIN', 'GERMANY', 'PARIS', 'FRANCE'),
   ('BERN', 'SWITZERLAND', 'CANBERRA', 'AUSTRALIA'),
   ('BERN', 'SWITZERLAND', 'HELSINKI', 'FINLAND'),
   ('BERN', 'SWITZERLAND', 'MADRID', 'SPAIN'),
   ('CAIRO', 'EGYPT', 'CANBERRA', 'AUSTRALIA'),
   ('CANBERRA', 'AUSTRALIA', 'OTTAWA', 'CANADA'),
   ('HELSINKI', 'FINLAND', 'STOCKHOLM', 'SWEDEN'),
   ('ISLAMABAD', 'PAKISTAN', 'CAIRO', 'EGYPT'),
   ('KABUL', 'AFGHANISTAN', 'BAGHDAD', 'IRAQ'),
   ('MADRID', 'SPAIN', 'BEIJING', 'CHINA'),
   ('MOSCOW', 'RUSSIA', 'TEHRAN', 'IRAN'),
   ('MOSCOW', 'RUSSIA', 'BEIJING', 'CHINA'),
   ('OTTAWA', 'CANADA', 'TOKYO', 'JAPAN'),
   ('OTTAWA', 'CANADA', 'BEIJING', 'CHINA'),
   ('OTTAWA', 'CANADA', 'CANBERRA', 'AUSTRALIA'),
   ('PARIS', 'FRANCE', 'BERLIN', 'GERMANY'),
   ('PARIS', 'FRANCE', 'HELSINKI', 'FINLAND'),
   ('PARIS', 'FRANCE', 'MADRID', 'SPAIN'),
   ('ROME', 

In [35]:
w2v_large_analogy_dummy[0]

0.19085141219811708

In [38]:
w2v_large_analogy_dummy[1]

[{'section': 'capital-common-countries',
  'correct': [('ATHENS', 'GREECE', 'ROME', 'ITALY'),
   ('BAGHDAD', 'IRAQ', 'KABUL', 'AFGHANISTAN'),
   ('BERLIN', 'GERMANY', 'PARIS', 'FRANCE'),
   ('BERN', 'SWITZERLAND', 'CANBERRA', 'AUSTRALIA'),
   ('BERN', 'SWITZERLAND', 'HELSINKI', 'FINLAND'),
   ('BERN', 'SWITZERLAND', 'MADRID', 'SPAIN'),
   ('CAIRO', 'EGYPT', 'CANBERRA', 'AUSTRALIA'),
   ('CANBERRA', 'AUSTRALIA', 'OTTAWA', 'CANADA'),
   ('HELSINKI', 'FINLAND', 'STOCKHOLM', 'SWEDEN'),
   ('ISLAMABAD', 'PAKISTAN', 'CAIRO', 'EGYPT'),
   ('KABUL', 'AFGHANISTAN', 'BAGHDAD', 'IRAQ'),
   ('MADRID', 'SPAIN', 'BEIJING', 'CHINA'),
   ('MOSCOW', 'RUSSIA', 'TEHRAN', 'IRAN'),
   ('MOSCOW', 'RUSSIA', 'BEIJING', 'CHINA'),
   ('OTTAWA', 'CANADA', 'TOKYO', 'JAPAN'),
   ('OTTAWA', 'CANADA', 'BEIJING', 'CHINA'),
   ('OTTAWA', 'CANADA', 'CANBERRA', 'AUSTRALIA'),
   ('PARIS', 'FRANCE', 'BERLIN', 'GERMANY'),
   ('PARIS', 'FRANCE', 'HELSINKI', 'FINLAND'),
   ('PARIS', 'FRANCE', 'MADRID', 'SPAIN'),
   ('ROME', 